<a href="https://colab.research.google.com/github/TejoramV/CS6910_Assignment2/blob/main/Assignment2_Part-A-Visualiztions.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.models import Model
from tensorflow.keras import layers

!pip install wandb
import wandb
from wandb.keras import WandbCallback
from PIL import Image

%matplotlib inline
%config InlineBackend.figure_format = 'svg'
import matplotlib.pyplot as plt
import matplotlib.image as mpimg

     |████████████████████████████████| 1.8 MB 4.6 MB/s 
     |████████████████████████████████| 181 kB 22.5 MB/s 
     |████████████████████████████████| 144 kB 30.9 MB/s 
     |████████████████████████████████| 63 kB 1.6 MB/s 
  Created wheel for pathtools: filename=pathtools-0.1.2-py3-none-any.whl size=8806 sha256=0c8fa2823711506fe06a06fc30ce1097a423a8f753dba26f59eea7f54f7dcf2c
  Stored in directory: /root/.cache/pip/wheels/3e/31/09/fa59cef12cdcfecc627b3d24273699f390e71828921b2cbba2
Successfully built pathtools


In [2]:
!wandb login
wandb.init(project="CS6910-Assignment-2-display", entity="tejoram")

wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: 
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


wandb: Currently logged in as: tejoram (use `wandb login --relogin` to force relogin)


In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [56]:
train_dir="/content/drive/MyDrive/inaturalist_12K/train"
train_data = tf.keras.preprocessing.image_dataset_from_directory(directory = train_dir, labels = 'inferred', label_mode = 'categorical', color_mode = 'rgb', image_size = (200, 200))
model=tf.keras.models.load_model("/content/drive/MyDrive/model.h5")

label=['Amphibia','Animalia','Arachnida','Aves','Fungi','Insecta','Mammalia','Mollusca','Plantae','Reptilia']
plt.figure(figsize=(10, 40))
data, labels = train_data.as_numpy_iterator().next()
for i in range(30):
    ax = plt.subplot(10, 3, i + 1)
    plt.imshow(data[i].astype("uint8"))
    predictions = label[np.argmax(model.predict(np.array(data[i,:,:,:]).reshape(1, 200, 200, 3)))]
    title_obj = plt.title('True label: {}\nPredicted label: {}'.format(label[np.where(labels[i] == 1)[0][0]],predictions))

    plt.axis("off")
wandb.run.name="Assignment2-Question-1_Output1"
wandb.log({'img': [wandb.Image(ax)]})

Found 10008 files belonging to 10 classes.


In [57]:
first_layer = tf.keras.models.Model(inputs = model.inputs, outputs = model.layers[2].output) 
data,_ = train_data.as_numpy_iterator().next()

predictions = np.array(first_layer.predict(np.array(data)))

fig, axs = plt.subplots(4, 8, figsize = (40, 40))
for i in range(32):
    axs[int(i/8), i%8].imshow(predictions[0,:,:,i])
    plt.axis("off")
wandb.run.name="Assignment2-Question-1_Output1"
wandb.log({'Filter_vis': [wandb.Image(fig)]})    

In [20]:
test_dir = "/content/drive/MyDrive/inaturalist_12K/val"
test = ImageDataGenerator(rescale=1./255)
test_data = test.flow_from_directory(test_dir, target_size=(200, 200), batch_size=256)
model=tf.keras.models.load_model("/content/drive/MyDrive/model.h5")
fifth_layer = tf.keras.models.Model([model.inputs],[model.get_layer("conv2d_4").output])

@tf.custom_gradient
def guidedRelU(x):
    def grad(dy):
        return tf.nn.relu(dy) 
    return tf.nn.relu(x), grad

for sweeper in model.layers[1:]:
    if hasattr(sweeper, 'activation') and sweeper.activation==tf.keras.activations.relu:
        sweeper.activation = guidedRelU

fig, axs = plt.subplots(10, 2, figsize=(10, 40))
images = tf.convert_to_tensor(test_data[0][0][:10], dtype=tf.float32)

for i in range(10):
    with tf.GradientTape() as fix:
        input = tf.expand_dims(images[i], 0)
        fix.watch(input)
        output = fifth_layer(input)[0]
    
    final_img = fix.gradient(output,input)[0]

    axs[i][0].set_title("Input Image")
    axs[i][0].imshow(images[i])
    axs[i][1].set_title("Images which excite this neuron")
    axs[i][1].imshow(final_img)


wandb.run.name="Assignment2-Question-1_Output3"
wandb.log({'Neuron_excitations': [wandb.Image(fig)]})    

Found 2008 images belonging to 10 classes.


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i